## Configurations and Dependencies

In [37]:
import pandas as pd # pip install pandas
import re # pip install re
import markdown # pip install markdown
from bs4 import BeautifulSoup # pip install beautifulsoup4
import csv
import emoji
import nltk

pd.set_option('display.max_columns', None)  # or 1000
pd.set_option('display.max_rows', None)  # or 1000
pd.set_option('display.max_colwidth', None)  # or 199

hot = pd.read_csv("../dataset/raw/hot.csv")
top = pd.read_csv("../dataset/raw/top.csv")
controversial = pd.read_csv("../dataset/raw/controversial.csv")
new = pd.read_csv("../dataset/raw/new.csv")

df_list = [hot, top, controversial, new, pd.concat([hot, top, controversial, new])]

## Preprocessing

#### Duplicates and Empty Cells

In [38]:
check_list = []

for df in df_list:
    check_list.append((df.duplicated().sum(), df.loc[:, ~df.columns.isin(['Content', 'Flair'])].isnull().sum().sum()))

count = 1
for check in check_list:
    if check != (0, 0): 
        count += 1
        print(f"ERROR AT DF {count}")
    count += 1

if count == len(check_list): print("ALL CLEAR")

In [39]:
for df in df_list[0:4]:
    df.insert(2, "Title+Content", df["Title"] + " " + df["Content"])

In [40]:
# Check 
for df in df_list[0:4]:
    display(df.head(1))

Timestamp Content Type  \
0  2024-04-21 13:01:23    Text-only   

                                                                                                                                                                                                                                                                                                                                                                                          Title+Content  \
0  E-SENA Help. I filed a request for assistance sa e-sena re last pay na inabot ng 2 months at coe last friday. Meron na akong ref number ng request for assistance. Kaso that same day, biglang nagmessage ang hr na okay na ang cheke ng last pay ko at pwede ko na sya ipick up. My question is paano icancel yung request for assistance since nakuha ko na yung last pay at coe ko. Thank you po!   

    Title  \
0  E-SENA   

                                                                                                                                                                                                                                                                                                                                                                                         Content  \
0  Help. I filed a request for assistance sa e-sena re last pay na inabot ng 2 months at coe last friday. Meron na akong ref number ng request for assistance. Kaso that same day, biglang nagmessage ang hr na okay na ang cheke ng last pay ko at pwede ko na sya ipick up. My question is paano icancel yung request for assistance since nakuha ko na yung last pay at coe ko. Thank you po!   

   Upvotes Count  Comments Count  Upvote Ratio            Flair  \
0              2               3           1.0  Advice Needed 🤔   

                                                      Permalink Reddit ID  
0  https://www.reddit.com//r/AntiworkPH/comments/1c99rt3/esena/   1c99rt3

Timestamp Content Type  \
0  2022-04-26 20:35:36    Text-only   

                                                                                                                                                                                                                                                                                                                       Title+Content  \
0  Name worst companies in PH to work with Before, I used to be scared of mentioning companies either I hated working or wasted my time on the recruitment.\n\nNow, I am not ashamed anymore. Hindi ko naman inaname drop ang pangalan ng workers, CEO, or HR; Just the company and experience.\n\nComment down below! I will start.   

                                     Title  \
0  Name worst companies in PH to work with   

                                                                                                                                                                                                                                                                                     Content  \
0  Before, I used to be scared of mentioning companies either I hated working or wasted my time on the recruitment.\n\nNow, I am not ashamed anymore. Hindi ko naman inaname drop ang pangalan ng workers, CEO, or HR; Just the company and experience.\n\nComment down below! I will start.   

   Upvotes Count  Comments Count  Upvote Ratio Flair  \
0           1558            1440           1.0   NaN   

                                                                                       Permalink  \
0  https://www.reddit.com//r/AntiworkPH/comments/ucbk2p/name_worst_companies_in_ph_to_work_with/   

  Reddit ID  
0    ucbk2p

Timestamp Content Type Title+Content  \
0  2022-11-03 11:30:05        Image           NaN   

                                                                                                                                Title  \
0  update: pati lunch break gusto na din nila icontrol. remind ko na yata sila na independent contractor kami, hindi empleyado nila 😒   

  Content  Upvotes Count  Comments Count  Upvote Ratio   Flair  \
0     NaN              0              54           0.5  Rant 😡   

                                                                                         Permalink  \
0  https://www.reddit.com//r/AntiworkPH/comments/ykr2zw/update_pati_lunch_break_gusto_na_din_nila/   

  Reddit ID  
0    ykr2zw

Timestamp Content Type  \
0  2024-04-21 15:32:18    Text-only   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      Title+Content  \
0  Can’t stay even for a minute longer! I’m a nurse working for almost a year sa isang gov’t hosp. The first month was really good for me since napakahealthy nung ward na una kong pinasukan, I was never absent if I’m not sick or had important appointments, I was never late kahit na wala naman akong sweldo as a volunteer but then I was transferred the next month to the surgical ward. Everything went downhill from there. \n\nMy confidence as a nurse.\nMy work-life balance.\nMy happiness.\nMy love for nursing.\nMy mental health.\n\nI became miserable so fast I couldn’t hold on to save myself. The workload was bearable but the coworkers was the worst. They were ganging up on me, even sa pinakamaliit na bagay pinapalaki nila but when their friends make the same mistakes that I do, they don’t bat an eye about it. It was clear that I was being bullied but I had to be strong sa ganitong work environment pero it lead me to go have myself get checked by a psychologist.\n\nUmiiyak ako before and after work.\nKinakabahan kapag tumutunog yung phone ko.\nNanlalamig kapag umaapak na sa hospital.\n4hours max lang yung tulog ko may duty or wala. \n\n\nNow, I’m resigning after months of enduring the toxicity of my work environment. Gusto kong mag’Immediate Resignation, kasi hindi ko na talaga kayang tumagal doon ng kahit isang minuto pa. Needed po ba talaga sa Public hospitals na magrender kahit isang week before umalis? And also, ayokong ilagay na Toxic work environment sa resignation ko since it might bounce back to my record if ever lilipat ako ng ibang hospital. Is Personal reasons enough po ba to immediate resign? Or should I put that its because of my mental health? I just want to run away from that place immediately.\n\nNeed opinions po and advice. Thank you.    

                                  Title  \
0  Can’t stay even for a minute longer!   

                                                                                                                                                                                                                                                                                        

#### Data Cleaning

In [35]:
URL_REGEX = r".*(https?:\/\/)?([\da-z\.-]+)\.([a-z\.]{2,6})([\/\w\.-]*).*"

# Remove URLs
def unurl(cell):
    return re.sub(URL_REGEX, "", str(cell))

# Convert markdown to plaintext 
def md_to_text(cell):
    html = markdown.markdown(cell)
    soup = BeautifulSoup(html, features='html.parser')
    return soup.get_text()

# Replace NaN and \n 
def cleantext(cell):
    return re.sub(r"(\n|NaN|nan)", " ", str(cell))

# Convert slangs
def unslang(cell):
    user_string = str(cell)
    user_string = user_string.split(" ")
    j = 0
    for _str in user_string:
        fileName = "slang.txt"
        accessMode = "r"
        with open(fileName, accessMode) as myCSVfile:
            dataFromFile = csv.reader(myCSVfile, delimiter="=")
            _str = re.sub('[^a-zA-Z0-9-_.]', '', _str)
            for row in dataFromFile:
                if _str.upper() == row[0].upper():
                    user_string[j] = row[1]
            myCSVfile.close()
        j = j + 1
    return ' '.join(user_string)

def unemoji(text):
    return emoji.replace_emoji(text, replace="")

In [36]:
count = 1
for df in df_list[0:4]:
    df['Title+Content'] = df['Title+Content'].apply(unurl)
    df['Title+Content'] = df['Title+Content'].apply(md_to_text)
    df['Title+Content'] = df['Title+Content'].apply(cleantext)
    df['Title+Content'] = df['Title+Content'].apply(unslang)
    df['Title+Content'] = df['Title+Content'].apply(unemoji)
    print(f"Cleaning DF {count}...")
    count += 1

Cleaning DF 1...
Cleaning DF 1...
Cleaning DF 1...
Cleaning DF 1...


#### Create `Title+Content`

In [11]:
df1.to_csv("../clean/hot.csv", index=False)
df1 = pd.read_csv("clean_csv/hot.csv")
df1

Timestamp Content Type  \
0    2023-04-07 10:17:53    Text-only   
1    2024-04-15 07:27:11        Image   
2    2024-04-15 08:28:04    Text-only   
3    2024-04-15 11:11:32    Text-only   
4    2024-04-15 11:26:21    Text-only   
5    2024-04-14 15:00:08    Text-only   
6    2024-04-14 23:27:20    Text-only   
7    2024-04-14 10:32:32    Text-only   
8    2024-04-14 20:13:10    Text-only   
9    2024-04-13 20:36:08      Unknown   
10   2024-04-13 15:58:38    Text-only   
11   2024-04-13 12:58:35    Text-only   
12   2024-04-13 10:02:27    Text-only   
13   2024-04-13 19:55:46    Text-only   
14   2024-04-13 07:24:27    Text-only   
15   2024-04-13 01:44:49    Text-only   
16   2024-04-13 01:29:08    Text-only   
17   2024-04-12 12:55:09    Text-only   
18   2024-04-12 11:40:02    Text-only   
19   2024-04-12 20:06:33    Text-only   
20   2024-04-12 19:33:49    Text-only   
21   2024-04-12 09:46:43    Text-only   
22   2024-04-12 10:39:42    Text-only   
23   2024-04-12 15:21:37    Text-only   
24   2024-04-12 08:33:37    Text-only   
25   2024-04-12 13:22:15    Text-only   
26   2024-04-12 02:26:02    Text-only   
27   2024-04-11 11:44:03    Text-only   
28   2024-04-11 11:18:11        Image   
29   2024-04-12 08:39:18    Text-only   
30   2024-04-11 10:15:34    Text-only   
31   2024-04-11 21:54:37    Text-only   
32   2024-04-11 02:35:39    Text-only   
33   2024-04-11 13:58:14    Text-only   
34   2024-04-11 14:31:28    Text-only   
35   2024-04-10 10:20:17    Text-only   
36   2024-04-10 15:39:18    Text-only   
37   2024-04-10 19:47:43    Text-only   
38   2024-04-10 17:08:33    Text-only   
39   2024-04-10 10:41:15    Text-only   
40   2024-04-09 21:40:39    Text-only   
41   2024-04-09 22:37:19    Text-only   
42   2024-04-10 08:02:30    Text-only   
43   2024-04-10 02:56:54    Text-only   
44   2024-04-10 00:59:00    Text-only   
45   2024-04-08 22:23:54    Text-only   
46   2024-04-08 23:23:40    Text-only   
47   2024-04-08 11:31:21        Image   
48   2024-04-08 07:44:32      Unknown   
49   2024-04-08 09:16:05    Text-only   
50   2024-04-08 22:39:39    Text-only   
51   2024-04-08 16:51:53    Text-only   
52   2024-04-08 22:20:39    Text-only   
53   2024-04-08 09:46:07    Text-only   
54   2024-04-08 17:03:18    Text-only   
55   2024-04-08 02:45:27    Text-only   
56   2024-04-07 20:39:56        Image   
57   2024-04-07 21:33:56    Text-only   
58   2024-04-07 12:33:52    Text-only   
59   2024-04-07 16:24:19    Text-only   
60   2024-04-07 19:49:08    Text-only   
61   2024-04-07 07:32:05    Text-only   
62   2024-04-06 11:03:28    Text-only   
63   2024-04-06 12:14:00    Text-only   
64   2024-04-06 05:56:04    Text-only   
65   2024-04-06 16:59:39    Text-only   
66   2024-04-06 14:14:46    Text-only   
67   2024-04-05 14:47:39    Text-only   
68   2024-04-05 20:41:49    Text-only   
69   2024-04-05 18:48:31      Unknown   
70   2024-04-06 09:07:38    Text-only   
71   2024-04-06 09:03:50    Text-only   
72   2024-04-05 20:58:32    Text-only   
73   2024-04-05 22:11:51    Text-only   
74   2024-04-05 18:20:47    Text-only   
75   2024-04-05 21:22:38    Text-only   
76   2024-04-05 21:22:05    Text-only   
77   2024-04-05 13:01:13    Text-only   
78   2024-04-05 09:43:53    Text-only   
79   2024-04-04 22:40:09    Text-only   
80   2024-04-05 17:44:41    Text-only   
81   2024-04-05 11:44:02    Text-only   
82   2024-04-05 14:40:21    Text-only   
83   2024-04-04 12:07:46    Text-only   
84   2024-04-04 16:17:19        Image   
85   2024-04-04 22:04:59      Unknown   
86   2024-04-04 09:38:25        Image   
87   2024-04-04 08:51:54        Image   
88   2024-04-05 00:53:09    Text-only   
89   2024-04-04 16:01:59    Text-only   
90   2024-04-04 13:04:38    Text-only   
91   2024-04-03 21:31:50    Text-only   
92   2024-04-04 07:48:48    Text-only   
93   2024-04-04 07:42:07    Text-only   
94   2024-04-03 18:04:10    Text-only   
95   2024-04-04 00:21:46    Text-only   
96   2024-04-03 11:36:26    Text-only 